In [1]:
import glob 
import gezi
from gezi import tqdm
import pandas as pd
import dask.dataframe as dd
from plotly.graph_objs import Scatter,Layout
import plotly
import plotly.offline as py
import numpy as np
import plotly.graph_objs as go
from plotly.subplots import make_subplots

#setting offilne
plotly.offline.init_notebook_mode(connected=True)
import plotly.express as px

In [2]:
marks = ['tuwen', 'video']

In [3]:
def deal(df):
  df.hour = df.hour.astype(str)
  df = df.groupby(['abtest', 'hour'], as_index=False).last()
  df = df.sort_values(by=['hour'])
  df = df.drop_duplicates()
  df.hour = pd.to_datetime(df.hour, format='%Y%m%d%H')
  return df

def gen_df(mark, abtest=8):
  root = f'/search/odin/publicData/CloudS/rank/infos/{mark}/{abtest}'  
  dfs_offline = []
  dfs_online = []
  for file in tqdm(glob.glob(f'{root}/*/sgsapp_metrics_offline.csv')):
    if not gezi.non_empty(file):
      continue
    df = pd.read_csv(file)
    dfs_offline.append(df)
  for file in tqdm(glob.glob(f'{root}/*/sgsapp_metrics_online.csv')):
    if not gezi.non_empty(file):
      continue
    df = pd.read_csv(file)
    dfs_online.append(df)
  df_off = deal(pd.concat(dfs_offline))
  df_off.name = mark + '_off'
  df_off.to_csv(f'{root}/sgsapp_metrics_offline.csv')
  df_on = deal(pd.concat(dfs_online))
  df_on.name = mark + '_on'
  df_on.to_csv(f'{root}/sgsapp_metrics_online.csv')
  return df_off, df_on

In [4]:
df_off_tuwen, df_on_tuwen = gen_df('tuwen')

100%|██████████| 241/241 [00:12<00:00, 19.63it/s]


In [5]:
df_tuwen = pd.concat([df_off_tuwen, df_on_tuwen])
# df_tuwen[df_tuwen.hour=='2020011309'][['abtest', 'Click/auc']]

In [6]:
df_off_video, df_on_video = gen_df('video')

100%|██████████| 284/284 [00:16<00:00, 17.58it/s]


In [7]:
df_video = pd.concat([df_off_video, df_on_video])

In [8]:
df_off_tuwen.set_index('hour').groupby(pd.Grouper(freq='D')).mean().head()

abtest  Click/all/auc  Click/auc  Click/clck/mse  \
hour                                                            
2020-01-11  45600.0            NaN   0.731087        0.077288   
2020-01-12      NaN            NaN        NaN             NaN   
2020-01-13      NaN            NaN        NaN             NaN   
2020-01-14  23200.0       0.747842   0.740895        0.078259   
2020-01-15  23200.0       0.733165   0.730241        0.076027   

            Click/click/dur_loss  Click/click/mae  Click/click/mean  \
hour                                                                  
2020-01-11              0.796231         0.213671               NaN   
2020-01-12                   NaN              NaN               NaN   
2020-01-13                   NaN              NaN               NaN   
2020-01-14              0.790806         0.212218               NaN   
2020-01-15              0.794252         0.214438               NaN   

            Click/click/time_auc  Click/click/weighted_time_auc  \
hour                                                              
2020-01-11              0.494857                       0.440975   
2020-01-12                   NaN                            NaN   
2020-01-13                   NaN                            NaN   
2020-01-14              0.496387                       0.459466   
2020-01-15              0.507977                       0.453725   

            Click/cold/auc  ...  stats/num_instances  stats/time_per_click  \
hour                        ...                                              
2020-01-11        0.801384  ...                  NaN              0.031136   
2020-01-12             NaN  ...                  NaN                   NaN   
2020-01-13             NaN  ...                  NaN                   NaN   
2020-01-14        0.843052  ...                  NaN              0.033564   
2020-01-15        0.734016  ...                  NaN              0.032146   

            stats/time_per_show  stats/time_per_user  stats/vtime_per_click  \
hour                                                                          
2020-01-11             0.311885             0.090753                    0.0   
2020-01-12                  NaN                  NaN                    NaN   
2020-01-13                  NaN                  NaN                    NaN   
2020-01-14             0.329076             0.086453                    0.0   
2020-01-15             0.328202             0.086594                    0.0   

            stats/vtime_per_show  stats/vtime_per_user  time_auc  vtime_auc  \
hour                                                                          
2020-01-11                   0.0                   0.0  0.681223        NaN   
2020-01-12                   NaN                   NaN       NaN        NaN   
2020-01-13                   NaN                   NaN       NaN        NaN   
2020-01-14                   0.0                   0.0  0.695764        NaN   
2020-01-15                   0.0                   0.0  0.685000        NaN   

            weighted_time_auc  
hour                           
2020-01-11           0.768912  
2020-01-12                NaN  
2020-01-13                NaN  
2020-01-14           0.771343  
2020-01-15           0.770796  

[5 rows x 377 columns]

In [9]:
x = df_off_tuwen.groupby([df_off_tuwen['hour'].dt.date])['auc'].mean()

In [10]:
df_off_tuwen.set_index('hour').resample('D')['auc'].mean().head()

hour
2020-01-11    0.686180
2020-01-12         NaN
2020-01-13         NaN
2020-01-14    0.703407
2020-01-15    0.691272
Freq: D, Name: auc, dtype: float64

In [11]:
x.to_frame().reset_index().head()

hour       auc
0  2020-01-11  0.686180
1  2020-01-14  0.703407
2  2020-01-15  0.691272
3  2020-01-16  0.680434
4  2020-02-08  0.712690

In [12]:
# df_tuwen2, df_on_tuwen2 = gen_df('tuwen', 8)
df_tuwen2, df_on_tuwen2 = gen_df('tuwen', 16)
df_tuwen2

100%|██████████| 360/360 [00:16<00:00, 19.42it/s]


abtest                hour  Click/all/auc  Click/auc  Click/clck/mse  \
155    1600 2020-01-03 11:00:00            NaN   0.727090             NaN   
359   45600 2020-01-03 11:00:00            NaN   0.751558             NaN   
156    1600 2020-01-03 12:00:00            NaN   0.734138             NaN   
360   45600 2020-01-03 12:00:00            NaN   0.746596             NaN   
157    1600 2020-01-03 13:00:00            NaN   0.741955             NaN   
..      ...                 ...            ...        ...             ...   
715   45600 2020-02-14 04:00:00       0.757052   0.728610        0.067319   
716   45600 2020-02-14 05:00:00       0.770810   0.740271        0.073218   
153     500 2020-02-14 05:00:00       0.780050   0.750787        0.074135   
154     500 2020-02-14 12:00:00       0.746560   0.743407        0.070571   
717   45600 2020-02-14 12:00:00       0.739894   0.734754        0.069829   

     Click/click/dur_loss  Click/click/mae  Click/click/time_auc  \
155                   NaN              NaN              0.492076   
359                   NaN              NaN              0.498486   
156                   NaN              NaN              0.507266   
360                   NaN              NaN              0.503321   
157                   NaN              NaN              0.517976   
..                    ...              ...                   ...   
715              0.785327         0.200358              0.511565   
716              0.789515         0.207781              0.503915   
153              0.790338         0.209428              0.512852   
154              0.798393         0.204033              0.511580   
717              0.797711         0.202681              0.499382   

     Click/click/weighted_time_auc  Click/cold/auc  ...  stats/click_ratio  \
155                       0.445584        0.837053  ...           0.186278   
359                       0.458104        0.812555  ...           0.166939   
156                       0.473947        0.829493  ...           0.181040   
360                       0.464105        0.833844  ...           0.171686   
157                       0.485781        0.800349  ...           0.178780   
..                             ...             ...  ...                ...   
715                       0.440269        0.909064  ...           0.162905   
716                       0.430340        0.916394  ...           0.169099   
153                       0.443436        0.934505  ...           0.165060   
154                       0.486264        0.803524  ...           0.179880   
717                       0.471249        0.821084  ...           0.179250   

     stats/time_per_click  stats/time_per_show  stats/time_per_user  \
155             88.062348            16.404104           250.512064   
359             88.889497            14.839120           247.054039   
156             91.231078            16.516439           255.005379   
360             92.244753            15.837175           244.432368   
157             98.056607            17.530534           279.356921   
..                    ...                  ...                  ...   
715              0.030765             0.300701             0.094857   
716              0.030897             0.313477             0.093896   
153              0.031291             0.309897             0.093748   
154              0.027358             0.295272             0.046664   
717              0.027049             0.290910             0.046404   

     stats/vtime_per_click  stats/vtime_per_show  stats/vtime_per_user  \
155                    NaN                   NaN                   NaN   
359                    NaN                   NaN                   NaN   
156                    NaN                   NaN                   NaN   
360                    NaN                   NaN                   NaN   
157                    NaN                   NaN                   NaN   
..                     ...   

In [13]:
df_video2, df_on_video2 = gen_df('video', 16)
df_video2

100%|██████████| 921/921 [00:41<00:00, 22.52it/s]


abtest                hour  Click/all/auc  Click/auc  Click/clck/mse  \
918    45600 2020-01-03 02:00:00            NaN   0.754569             NaN   
717     1600 2020-01-03 02:00:00            NaN   0.765245             NaN   
919    45600 2020-01-03 13:00:00            NaN   0.738942             NaN   
718     1600 2020-01-03 13:00:00            NaN   0.745437             NaN   
719     1600 2020-01-03 14:00:00            NaN   0.746310             NaN   
...      ...                 ...            ...        ...             ...   
1834   45600 2020-02-14 19:00:00       0.747323   0.731315        0.101572   
1835   45600 2020-02-14 20:00:00       0.752474   0.735823        0.100659   
715      500 2020-02-14 20:00:00       0.744564   0.730535        0.102477   
716      500 2020-02-14 21:00:00       0.757161   0.732869        0.098556   
1836   45600 2020-02-14 21:00:00       0.755238   0.733879        0.099547   

      Click/click/dur_loss  Click/click/mae  Click/click/time_auc  \
918                    NaN              NaN              0.539105   
717                    NaN              NaN              0.500988   
919                    NaN              NaN              0.503609   
718                    NaN              NaN              0.499686   
719                    NaN              NaN              0.502061   
...                    ...              ...                   ...   
1834              0.744538         0.234792              0.510375   
1835              0.745567         0.232680              0.511071   
715               0.749080         0.234973              0.499457   
716               0.746520         0.234297              0.498089   
1836              0.746302         0.234407              0.506761   

      Click/click/weighted_time_auc  Click/cold/auc  ...  \
918                        0.496854        0.927771  ...   
717                        0.403695        0.925579  ...   
919                        0.471285        0.797862  ...   
718                        0.454450        0.787588  ...   
719                        0.459507        0.812990  ...   
...                             ...             ...  ...   
1834                       0.460912        0.935959  ...   
1835                       0.454831        0.926546  ...   
715                        0.435536        0.906787  ...   
716                        0.462148        0.950179  ...   
1836                       0.461468        0.942311  ...   

      stats/time_per_click  stats/time_per_show  stats/time_per_user  \
918             175.662916            17.952899           196.465103   
717             153.758514            15.758845           169.791453   
919             172.930360            20.152884           202.448091   
718             174.719956            19.865990           199.460038   
719             165.310154            19.444734           205.060305   
...                    ...                  ...                  ...   
1834              0.050440             0.381166             0.071622   
1835              0.049568             0.377010             0.074989   
715               0.048909             0.381121             0.073007   
716               0.050024             0.394802             0.079154   
1836              0.049760             0.382309             0.076099   

      stats/vtime_per_click  stats/vtime_per_show  stats/vtime_per_user  \
918                     NaN                   NaN                   NaN   
717                     NaN                   NaN                   NaN   
919                     NaN                   NaN                   NaN   
718                     NaN                   NaN                   NaN   
719                     NaN                   NaN                   NaN   
...                     ...                   ...                   ...   
1834               5.610201              5.816620              7.966185   
1835               5.642650              5.843157     

In [14]:
abid = 16
df_tuwen = pd.concat([df_tuwen2[df_tuwen2.abtest==45600].assign(abid=abid), \
#                       df_on_tuwen2[df_on_tuwen2.abtest==456].assign(abid=456), \
                      df_off_tuwen[df_off_tuwen.abtest==45600][df_off_tuwen.hour>=df_tuwen2.hour.values.min()].assign(abid=16)])
df_video = pd.concat([df_video2[df_video2.abtest==45600].assign(abid=abid), \
#                       df_on_video2[df_on_video2.abtest==456].assign(abid=456), \
                      df_off_video[df_off_video.abtest==45600][df_off_video.hour>=df_video2.hour.values.min()].assign(abid=16)])

In [15]:
df_cmp_tuwen = pd.concat([df_tuwen2[df_tuwen2.abtest==1600], df_on_tuwen2[df_on_tuwen2.abtest==16], \
                          df_on_tuwen2[df_on_tuwen2.abtest==456], \
                          df_off_tuwen[df_off_tuwen.abtest==45600][df_off_tuwen.hour>=df_tuwen2.hour.values.min()]])
df_cmp_video = pd.concat([df_video2[df_video2.abtest==1600], df_on_video2[df_on_video2.abtest==16], \
                          df_on_video2[df_on_video2.abtest==456], \
                          df_off_video[df_off_video.abtest==45600][df_off_video.hour>=df_video2.hour.values.min()]])
px.line(df_cmp_tuwen, x='hour', y='auc', color='abtest')

In [16]:
px.line(df_cmp_tuwen, x='hour', y='group/auc', color='abtest')

In [17]:
px.line(df_cmp_tuwen, x='hour', y='click/time_auc', color='abtest')

In [18]:
px.line(df_cmp_video, x='hour', y='auc', color='abtest')

In [19]:
px.line(df_cmp_tuwen, x='hour', y='group/click/time_auc', color='abtest')

In [20]:
px.line(df_tuwen, x='hour', y='auc', color='abid')

In [21]:
px.line(df_tuwen, x='hour', y='all/auc', color='abid')

In [22]:
px.line(df_tuwen, x='hour', y='group/auc', color='abid')

In [23]:
px.line(df_tuwen, x='hour', y='click/time_auc', color='abid')

In [24]:
px.line(df_tuwen, x='hour', y='group/click/time_auc', color='abid')

In [25]:
px.line(df_video, x='hour', y='auc', color='abid')

In [26]:
px.line(df_video, x='hour', y='group/auc', color='abid')

In [27]:
px.line(df_video, x='hour', y='click/time_auc', color='abid')
# px.line(df_video, x='hour', y='weighted_time_auc', color='abid')

In [28]:
px.line(df_video, x='hour', y='group/click/time_auc', color='abid')

In [29]:
abids = [456,16,8]
px.line(df_on_tuwen[df_on_tuwen.abtest.isin(abids)], x='hour', y='auc', color='abtest')

In [30]:
px.line(df_on_tuwen[df_on_tuwen.abtest.isin(abids)], x='hour', y='click/time_auc', color='abtest')

In [31]:
px.line(df_video, x='hour', y='vtime_auc', color='abid')

In [32]:
px.line(df_on_tuwen[df_on_tuwen.abtest.isin(abids)], x='hour', y='group/auc', color='abtest')

In [33]:
px.line(df_on_tuwen[df_on_tuwen.abtest.isin(abids)], x='hour', y='group/click/time_auc', color='abtest')

In [34]:
px.line(df_on_video[df_on_video.abtest.isin(abids)], x='hour', y='auc', color='abtest')

In [35]:
px.line(df_on_video[df_on_video.abtest.isin(abids)], x='hour', y='group/auc', color='abtest')

In [36]:
px.line(df_on_video[df_on_video.abtest.isin(abids)], x='hour', y='click/time_auc', color='abtest')

In [37]:
px.line(df_on_video[df_on_video.abtest.isin(abids)], x='hour', y='group/click/time_auc', color='abtest')

In [38]:
abids2 = [456, 16, 1600, 45600]
px.line(df_tuwen[df_tuwen.abtest.isin(abids2)], x='hour', y='auc', color='abtest')

In [39]:
abids2 = [456, 16, 1600, 45600]
px.line(df_tuwen[df_tuwen.abtest.isin(abids2)], x='hour', y='stats/click_ratio', color='abtest')

In [40]:
px.line(df_tuwen[df_tuwen.abtest.isin(abids2)], x='hour', y='group/auc', color='abtest')

In [41]:
px.line(df_tuwen[df_tuwen.abtest.isin(abids2)], x='hour', y='group/click/time_auc', color='abtest')

In [42]:
px.line(df_video[df_video.abtest.isin(abids2)], x='hour', y='auc', color='abtest')

In [43]:
px.line(df_video[df_video.abtest.isin(abids2)], x='hour', y='group/auc', color='abtest')

In [44]:
px.line(df_video[df_video.abtest.isin(abids2)], x='hour', y='group/click/time_auc', color='abtest')

In [45]:
def show(df, metric='auc', abids=abids, offline=False):
  if 'off' in df.name:
    offline = True
  if offline:
    abids = [x * 100 for x in abids]
  fig = px.line()
  for abid in abids:
    df_ = df[df.abtest==abid]
    fig.add_scatter(x=df_.hour, y=gezi.smooth(df_[metric].values, 0.), mode='lines', name=abid)
  fig.update_layout(
      title=df.name + ':' + metric,
#       xaxis_title='hour',
#       yaxis_title=metric,
  )
  py.iplot(fig)

In [46]:
# show(df_on_tuwen)

In [47]:
# show(df_on_tuwen, 'group/auc')

In [48]:
# show(df_on_tuwen, 'click/time_auc')

In [49]:
# show(df_on_tuwen, 'group/click/time_auc')

In [50]:
# show(df_on_video)

In [51]:
# show(df_on_video, 'group/auc')

In [52]:
# show(df_on_video, 'click/time_auc')

In [53]:
# show(df_on_video, 'group/click/time_auc')

In [54]:
def compare(df, metric='auc', smoothing=0., abids=abids, offline=False):
    if isinstance(abids, str):
        abids = [int(x) for x in abids.split(',')]
    if 'off' in df.name:
        offline = True
    if offline:
        abids = [x * 100 for x in abids]

    df_ = df

    datas = []
    for abid in abids:
        df = df_[df_.abtest==abid]
        df = df.fillna(0.4)
        if not len(df):
            continue
        data = go.Scatter(
            x=df.hour,
            y=gezi.smooth(df[metric].values, smoothing),
            mode='lines+markers',
            line_shape='spline',
            line_smoothing=1.,
            name=str(abid) 
        )

        datas.append(data)

    layout = go.Layout(xaxis=dict(type='date'), title=f'{df_.name}:{metric}', hovermode='x')
    fig = go.Figure(data=datas, layout=layout)
    py.iplot(fig)

In [55]:
compare(df_off_tuwen, 'group/auc')

In [56]:
compare(df_on_tuwen, 'group/auc')

In [57]:
compare(df_on_tuwen, 'group/click/time_auc')

In [58]:
compare(df_off_tuwen, 'group/auc')

In [59]:
compare(df_off_tuwen, 'auc')

In [60]:
df_off_tuwen[df_off_tuwen.abtest==45600].sort_values('hour', ascending=False)[['hour', 'click/time_auc']]

hour  click/time_auc
380 2020-02-14 21:00:00        0.603970
379 2020-02-14 20:00:00        0.611916
378 2020-02-14 19:00:00        0.608539
377 2020-02-14 18:00:00        0.612811
376 2020-02-14 17:00:00        0.614339
..                  ...             ...
194 2020-01-14 10:00:00        0.613389
193 2020-01-14 09:00:00        0.613442
192 2020-01-14 07:00:00        0.619071
191 2020-01-14 06:00:00        0.602022
190 2020-01-11 20:00:00        0.630842

[191 rows x 2 columns]

In [61]:
compare(df_off_tuwen, 'click/time_auc')

In [62]:
compare(df_off_tuwen, 'group/click/time_auc')

In [63]:
compare(df_on_tuwen, 'group/click/time_auc')

In [64]:
from projects.common.monitor.tarus import Tarus
from projects.common.monitor.show import show

ModuleNotFoundError: No module named 'projects.common.monitor.tarus'

In [ ]:
last_days = 50
abids = [15]
worker_days = Tarus()
worker_days.init(abids, last_days, 'daily')
dfs_days, diffs_days = worker_days.run()

def show_days(name, diffs=None):
  figs = show(dfs_days, name, worker_days.stats, abids, mark='daily', diffs=diffs)
  for fig in figs:
    py.iplot(fig)

In [ ]:
%%html
<style>
.output_wrapper, .output {
    height:auto !important;
    max-height:10000px;  /* your desired max-height here */
}
.output_scroll {
    box-shadow:none !important;
    webkit-box-shadow:none !important;
}
</style>

In [ ]:
# show_days('tuwen')

In [ ]:
dfs_days['tuwen']

In [ ]:
fig = px.line()
df = df_on_tuwen
metric = 'group/click/time_auc'
metric = 'click/time_auc'
abid = 456
df_ = df[df.abtest==abid]
fig.add_scatter(x=df_.hour, y=gezi.smooth(df_[metric].values * 3, 0.8), mode='lines', name=metric)
df_ = dfs_days['tuwen']
df_.hour = pd.to_datetime(df_.date, format='%Y%m%d')
fig.add_scatter(x=df_.hour, y=gezi.smooth(df_.dur2.values / 5., 0.8), mode='lines', name='dur2')
py.iplot(fig)